## Notebook to fetch and compile stonycreek into one excel file

In [39]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import xlsxwriter
import plotly.express as px
from datetime import datetime
import plotly.graph_objects as go
from datetime import datetime
from plotly.subplots import make_subplots
import requests
import io
import ipywidgets as widgets
from ipywidgets import HBox, VBox, interact
import numpy as np
from IPython.display import display
import re
from urllib.error import HTTPError
from pandas.errors import InvalidIndexError
from IPython.display import display, HTML, clear_output

pd.options.plotting.backend = "plotly"

In [49]:
SITE_PREFIX = "FCC"
SITE_NUMBERS = [f"0{x}" for x in (1, 2, 3, 4, 5, 6, 7, 8, 9, 11)] + ['10']
SITE_NAMES = [f"{SITE_PREFIX}{x}" for x in SITE_NUMBERS]
print(SITE_NAMES)
BASE_URL = "https://www.bosl.com.au/IoT/FCC/databases/"

['FCC01', 'FCC02', 'FCC03', 'FCC04', 'FCC05', 'FCC06', 'FCC07', 'FCC08', 'FCC09', 'FCC011', 'FCC10']


In [41]:
all_depth_vel_v1 = []
#all_depth_vel_v2 = []
#all_turb_temp_ec = []

def hit_website(url, **args):
    try:
        try:
            data = pd.read_csv(url, **args).dropna(how='all', axis='columns')
        except pd.errors.ParserError as e:
            print("Failed on:", url)
            raise e

        print(f"Hit: {url}")
        return data
    except HTTPError:
        print(f"Missed: {url}")
        return None

for site in SITE_NAMES:
    all_depth_vel_v1.append(hit_website(f"{BASE_URL}{site}.csv", names=[(x) for x in range(12)], skiprows=[0, 1]))
    #all_depth_vel_v2.append(hit_website(f"{BASE_URL}{site}_v2.csv"))
    #all_turb_temp_ec.append(hit_website(f"{BASE_URL}{site}_Dep_Turb.csv", 'warn', None, 1))

    # Misc data cleaning
    # 05-1 has extra row
    #if site == f"{SITE_PREFIX}05-1":
    #    all_data_v1[-1].drop(all_data_v1[-1].tail(1).index, inplace=True)

Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC01.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC02.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC03.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC04.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC05.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC06.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC07.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC08.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC09.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC011.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC10.csv


In [42]:
for data_v1 in all_depth_vel_v1:
    if data_v1 is not None:
        data_v1.rename(columns={0:"DateTime", 7:"Peaks", 5:"Angle", 8:"Course_depth"}, inplace=True)

In [43]:
site_id = widgets.Dropdown(
    options=SITE_NAMES,
    description='Site:',
    disabled=False,
    value=SITE_NAMES[0]
)
def response(change):
    clear_output()
    display(site_id)
    idx = SITE_NAMES.index(site_id.value)
    display(all_depth_vel_v1[idx])
site_id.observe(response)
response(None)

Dropdown(description='Site:', options=('FCC01', 'FCC02', 'FCC03', 'FCC04', 'FCC05', 'FCC06', 'FCC07', 'FCC08',…

DateTime  1     4  Angle    6  \
0     30/11/22 04:27:18 AM  T  3307   2.69  297   
1     30/11/22 04:34:24 AM  T  3316   2.58  294   
2     06/12/22 06:03:28 AM  T  4061   3.33  292   
3     06/12/22 06:10:38 AM  T  4061   3.28  298   
4     06/12/22 06:17:42 AM  T  4060   4.07  286   
...                    ... ..   ...    ...  ...   
1467  13/12/22 03:05:08 AM  T  4020  73.74  247   
1468  13/12/22 03:12:11 AM  T  4021  73.76  275   
1469  13/12/22 03:12:13 AM  T  4021  73.76  275   
1470  13/12/22 03:19:16 AM  T  4020  73.71  273   
1471  13/12/22 03:26:20 AM  T  4010  73.81  211   

                                Peaks  Course_depth      9  10    11  
0     1260B40|4360160|6600132|7C8011A           300  10.96   0   294  
1     1260C98|677013E|2540132|3D1011E           300  10.64   0   294  
2     1030A66|829013E|1E40136|65A0130           240  26.07   0   259  
3     1030A04|1D80138|6570132|3350126           240  32.05   0   259  
4     1014154|1D60388|2C20144|5680124           300  22.84   0   257  
...                               ...           ...    ...  ..   ...  
1467  59B03B4|2540152|6700124|38C0122          1440  12.28   0  1435  
1468  599043A|1070140|6D60120|7ED011A          1440  11.72   0  1433  
1469  599043A|1070140|6D60120|7ED011A          1440  11.72   0  1433  
1470  5AE037E|16D0170|248012E|3A50126          1440  11.14   0  1454  
1471  59901DC|24C0176|1160156|3CC0152          1500  11.25   0  1433  

[1472 rows x 10 columns]

In [45]:
all_merged_data = []
for idx, data_v1 in enumerate(all_depth_vel_v1):
    merged_data = data_v1
    merged_data.columns = merged_data.columns.astype(str)
    merged_data.dropna(how='all', subset=merged_data.columns, inplace=True)
    merged_data.dropna(axis=1, inplace=True, how='all')
    merged_data.dropna(subset=["Peaks"], inplace=True)
    try:
        def extract_peak(row):
            peaks = str(row["Peaks"]).split("|")
            try:
                decoded_peaks = [int(x[:3], 16) for x in peaks]
            except ValueError:
                decoded_peaks = [None] * len(peaks)
            finally:
                column_names = [f"DIST-{i+1}" for i in range(len(decoded_peaks))]
                return pd.Series(decoded_peaks, index=column_names)
        merged_data = pd.concat([merged_data, merged_data.apply(extract_peak, axis=1)], axis=1)
        depth_column_names = [col for col in merged_data.columns if 'DIST-' in col]
        
        merged_data["DateTime"] = pd.to_datetime(merged_data["DateTime"], format="%d/%m/%y %I:%M:%S %p")
        merged_data["DateTime"] =  merged_data["DateTime"].dt.tz_localize("UTC").dt.tz_convert("Australia/Broken_Hill")
        merged_data.dropna(subset=depth_column_names, axis='rows', inplace=True)

        all_merged_data.append(merged_data)
        merged_data.dropna(how='all', axis=1, inplace=True)
    except ValueError as e:
        print(merged_data)
        raise e
merged_data.dropna(how='all', axis=1, inplace=True)

In [46]:
KEEP_COLUMNS = ["DateTime", "SignalStrength", "Angle", "Peaks", "Velocity", "Course_depth"]
for merged_data in all_merged_data:
    columns_to_drop = [x for x in merged_data.columns if x not in KEEP_COLUMNS and "DIST-" not in x]
    merged_data.drop(columns_to_drop, axis=1, inplace=True)

In [47]:
site_id = widgets.Dropdown(
    options=SITE_NAMES,
    description='Site:',
    disabled=False,
    value=SITE_NAMES[0]
)
def response(change):
    clear_output()
    display(site_id)
    idx = SITE_NAMES.index(site_id.value)
    display(all_merged_data[idx])
site_id.observe(response)
response(None)

Dropdown(description='Site:', options=('FCC01', 'FCC02', 'FCC03', 'FCC04', 'FCC05', 'FCC06', 'FCC07', 'FCC08',…

DateTime  Angle                            Peaks  \
0    2022-11-30 14:57:18+10:30   2.69  1260B40|4360160|6600132|7C8011A   
1    2022-11-30 15:04:24+10:30   2.58  1260C98|677013E|2540132|3D1011E   
2    2022-12-06 16:33:28+10:30   3.33  1030A66|829013E|1E40136|65A0130   
3    2022-12-06 16:40:38+10:30   3.28  1030A04|1D80138|6570132|3350126   
4    2022-12-06 16:47:42+10:30   4.07  1014154|1D60388|2C20144|5680124   
...                        ...    ...                              ...   
1467 2022-12-13 13:35:08+10:30  73.74  59B03B4|2540152|6700124|38C0122   
1468 2022-12-13 13:42:11+10:30  73.76  599043A|1070140|6D60120|7ED011A   
1469 2022-12-13 13:42:13+10:30  73.76  599043A|1070140|6D60120|7ED011A   
1470 2022-12-13 13:49:16+10:30  73.71  5AE037E|16D0170|248012E|3A50126   
1471 2022-12-13 13:56:20+10:30  73.81  59901DC|24C0176|1160156|3CC0152   

      Course_depth  DIST-1  DIST-2  DIST-3  DIST-4  
0              300     294    1078    1632    1992  
1              300     294    1655     596     977  
2              240     259    2089     484    1626  
3              240     259     472    1623     821  
4              300     257     470     706    1384  
...            ...     ...     ...     ...     ...  
1467          1440    1435     596    1648     908  
1468          1440    1433     263    1750    2029  
1469          1440    1433     263    1750    2029  
1470          1440    1454     365     584     933  
1471          1500    1433     588     278     972  

[1472 rows x 8 columns]

Depth correction

In [50]:
CORRECTION_FACTORS = {'01':0, '02':0, '03':0, '04':0, '05':0, '06':0, '07':0, '08':0, '09':0, '10':0, '011':0}
for key, value in CORRECTION_FACTORS.items():
    idx = SITE_NUMBERS.index(key)
    all_merged_data[idx]["DEPTH-True"] = value - all_merged_data[idx]["DIST-1"].multiply(np.sin(np.radians(all_merged_data[idx]["Angle"])), axis="index")

Negative depths are removed

In [51]:
pd.DataFrame(zip(SITE_NAMES, (len(merged_data[merged_data["DEPTH-True"] < 0]) for merged_data in all_merged_data))).rename(columns={0:"Site", 1:"<0 Depths"})

Site  <0 Depths
0    FCC01       1457
1    FCC02      10102
2    FCC03        184
3    FCC04        586
4    FCC05      18338
5    FCC06          0
6    FCC07          1
7    FCC08       1282
8    FCC09       2437
9   FCC011       1239
10   FCC10       2926

In [52]:
site_id = widgets.Dropdown(
    options=SITE_NAMES,
    description='Site:',
    disabled=False,
    value=SITE_NAMES[0]
)
def response(change):
    clear_output()
    display(site_id)
    idx = SITE_NAMES.index(site_id.value)
    display(all_merged_data[idx].loc[all_merged_data[idx]["DEPTH-True"] < 0])
site_id.observe(response)
response(None)

Dropdown(description='Site:', options=('FCC01', 'FCC02', 'FCC03', 'FCC04', 'FCC05', 'FCC06', 'FCC07', 'FCC08',…

DateTime  Angle                            Peaks  \
0    2022-11-30 14:57:18+10:30   2.69  1260B40|4360160|6600132|7C8011A   
1    2022-11-30 15:04:24+10:30   2.58  1260C98|677013E|2540132|3D1011E   
2    2022-12-06 16:33:28+10:30   3.33  1030A66|829013E|1E40136|65A0130   
3    2022-12-06 16:40:38+10:30   3.28  1030A04|1D80138|6570132|3350126   
4    2022-12-06 16:47:42+10:30   4.07  1014154|1D60388|2C20144|5680124   
...                        ...    ...                              ...   
1467 2022-12-13 13:35:08+10:30  73.74  59B03B4|2540152|6700124|38C0122   
1468 2022-12-13 13:42:11+10:30  73.76  599043A|1070140|6D60120|7ED011A   
1469 2022-12-13 13:42:13+10:30  73.76  599043A|1070140|6D60120|7ED011A   
1470 2022-12-13 13:49:16+10:30  73.71  5AE037E|16D0170|248012E|3A50126   
1471 2022-12-13 13:56:20+10:30  73.81  59901DC|24C0176|1160156|3CC0152   

      Course_depth  DIST-1  DIST-2  DIST-3  DIST-4   DEPTH-True  
0              300     294    1078    1632    1992   -13.798041  
1              300     294    1655     596     977   -13.234198  
2              240     259    2089     484    1626   -15.044468  
3              240     259     472    1623     821   -14.818824  
4              300     257     470     706    1384   -18.240620  
...            ...     ...     ...     ...     ...          ...  
1467          1440    1435     596    1648     908 -1377.601436  
1468          1440    1433     263    1750    2029 -1375.821407  
1469          1440    1433     263    1750    2029 -1375.821407  
1470          1440    1454     365     584     933 -1395.628098  
1471          1500    1433     588     278     972 -1376.170608  

[1457 rows x 9 columns]

In [86]:
# for merged_data in all_merged_data:
#     merged_data.drop(merged_data[merged_data["DEPTH-True"] < 0].index, inplace=True)

Velocity correction

In [87]:
# for merged_data in all_merged_data:
#     merged_data["Corrected Velocity"] = merged_data["Velocity"] / np.cos(np.radians(merged_data["Angle"]))
# display(merged_data)

DateTime  Angle  Velocity  \
0    2022-10-17 12:30:31+10:30  -7.04       251   
1    2022-10-17 12:36:19+10:30  -7.82       302   
2    2022-10-17 12:42:08+10:30  78.72       278   
3    2022-10-17 12:48:04+10:30  67.89       299   
4    2022-10-17 12:54:03+10:30  67.85       303   
...                        ...    ...       ...   
2415 2022-12-10 06:05:46+10:30  73.59       292   
2416 2022-12-10 06:11:38+10:30  74.30       247   
2417 2022-12-10 06:11:40+10:30  74.30       247   
2418 2022-12-10 06:17:32+10:30  73.58       297   
2419 2022-12-10 06:23:37+10:30  73.64       296   

                                Peaks  SignalStrength  DIST-1  DIST-2  DIST-3  \
0     1B7115C|2A10194|46B013A|6410122           27595     439     673    1131   
1     4150154|78E0142|1E50140|8A50124             220    1045    1934     485   
2     1AD01C0|5D70172|798016E|29E0140           31368     429    1495    1944   
3     17702A8|24C0188|6DC013E|3760134           61388     375     588    1756   
4     2100304|397015C|4FC0154|71E0126           18704     528     919    1276   
...                               ...             ...     ...     ...     ...   
2415  54F034A|190022C|44A0156|265014E           14078    1359     400    1098   
2416  56E02F0|19A0258|3D10142|2AD012E           30504    1390     410     977   
2417  56E02F0|19A0258|3D10142|2AD012E           30504    1390     410     977   
2418  57402AC|19A0266|480011C|6FB0110           53576    1396     410    1152   
2419  56E02D6|19A0228|448016A|2FA0166           45297    1390     410    1096   

      DIST-4   DEPTH-True  Corrected Velocity  
0       1601  1823.804824          252.906707  
1       2213  1912.184163          304.834840  
2        670  1349.286994         1421.240041  
3        886  1422.576393          794.397310  
4       1822  1280.966421          803.643889  
...      ...          ...                 ...  
2415     613   466.359297         1033.595813  
2416     685   431.858472          912.784896  
2417     685   431.858472          912.784896  
2418    1787   430.935357         1050.671728  
2419     762   436.279915         1050.868942  

[7347 rows x 11 columns]

In [53]:
fig = px.line(all_merged_data[0], x='DateTime', y=depth_column_names)
f2 = go.FigureWidget(fig)
site_id = widgets.Dropdown(
    options=SITE_NAMES,
    description='Site:',
    disabled=False,
)

def response(change):
    f2.update_layout(title=f"Depth data of {site_id.value}")
    site_idx = SITE_NAMES.index(site_id.value)
    with f2.batch_update():
        for idx, col in enumerate(depth_column_names):
            f2.data[idx].x = all_merged_data[site_idx]["DateTime"]
            f2.data[idx].y = all_merged_data[site_idx][col]
site_id.observe(response, names="value")
response(None)
widgets.VBox([site_id, f2])

In [54]:
earliest_date = np.min(list(x["DateTime"].min() for x in all_merged_data)).date()
latest_date = np.max(list(x["DateTime"].max() for x in all_merged_data)).date()

url = f"https://api.melbournewater.com.au/rainfall-river-level/228378A/rain/hourly/range.csv?fromDate={earliest_date}&toDate={latest_date}"
print(url)
r = requests.get(url)
d = r.headers['content-disposition']
rain_filename = re.findall("filename=(.+)", d)[0]
rainfall_data = pd.read_csv(io.StringIO(r.content.decode('utf-8'))).dropna(how='all', axis='columns')

https://api.melbournewater.com.au/rainfall-river-level/228378A/rain/hourly/range.csv?fromDate=2022-09-13&toDate=2022-12-13


In [55]:
rainfall_data["Date/Time"] = pd.to_datetime(rainfall_data["Date/Time"], format="%Y/%m/%d %H:%M:%S").dt.tz_localize("Australia/Broken_Hill")
rainfall_data

Date/Time  Current rainfall (mm)  \
0    2022-12-13 14:00:00+10:30                    0.6   
1    2022-12-13 13:00:00+10:30                    0.4   
2    2022-12-13 12:00:00+10:30                    0.0   
3    2022-12-13 11:00:00+10:30                    0.0   
4    2022-12-13 10:00:00+10:30                    0.0   
...                        ...                    ...   
2191 2022-09-13 05:00:00+09:30                    0.0   
2192 2022-09-13 04:00:00+09:30                    0.0   
2193 2022-09-13 03:00:00+09:30                    0.0   
2194 2022-09-13 02:00:00+09:30                    0.0   
2195 2022-09-13 01:00:00+09:30                    0.0   

      Cumulative rainfall (mm)  
0                          1.0  
1                          0.4  
2                          0.0  
3                          0.0  
4                          0.0  
...                        ...  
2191                       0.0  
2192                       0.0  
2193                       0.0  
2194                       0.0  
2195                       0.0  

[2196 rows x 3 columns]

In [56]:
fig = rainfall_data.plot(x='Date/Time', y="Current rainfall (mm)", title=f"Rainfall of {rain_filename}").update_layout(
    xaxis_title="Time", yaxis_title=f"Rainfall (mm)"
)
fig.show()

Periods in which there is a >1 hr gap is ignored

In [57]:
time_filter = lambda x: x > 1 * 60 * 60

In [93]:
# fig = make_subplots(specs=[[{"secondary_y": True}]])
# fig.add_trace(go.Scatter(x=merged_data["DateTime"],
#     y=np.where(time_filter(merged_data['DateTime'].diff().dt.seconds), None, merged_data["DEPTH-True"]), 
#     name="Depth"),
#     secondary_y=False)
# fig.add_trace(go.Scatter(x=rainfall_data["Date/Time"], y=rainfall_data["Current rainfall (mm)"], name="Rainfall"), secondary_y=True)
# fig.update_yaxes(title_text="Depth (mm)", secondary_y=False)
# fig.update_yaxes(autorange="reversed", secondary_y=True)
# fig.update_yaxes(title_text="Rainfall (mm)", secondary_y=True)
# fig.update_xaxes(title_text="Time", tickangle=45, nticks=30)
# fig.update_layout(autosize=True, width=1100, height=700, legend=dict(title="Lines"), title=f"Rainfall vs Depth of {site}")
# fig.show()

In [59]:
fig = make_subplots(specs=[[{"secondary_y": True}]])
def display_col(source, col):
    for site_name, data in zip(SITE_NAMES, source):
        fig.add_trace(go.Scatter(x=data["DateTime"],
        y=np.where(time_filter(data['DateTime'].diff().dt.seconds), None, data[col]), 
        name=f"{col}:{site_name}"),
        secondary_y=False)

display_col(all_merged_data, "DIST-1")
display_col(all_merged_data, "DIST-2")
display_col(all_merged_data, "DIST-3")
display_col(all_merged_data, "DIST-4")

fig.add_trace(go.Scatter(x=rainfall_data["Date/Time"], y=rainfall_data["Current rainfall (mm)"], name="Rainfall"), secondary_y=True)
# fig.update_yaxes(title_text="Depth (mm)", secondary_y=False, range = [0, 8000])
max_rainfall = rainfall_data["Current rainfall (mm)"].max()
fig.update_yaxes(range = [max_rainfall * 4, 0], secondary_y=True, title_text="Rainfall (mm)")
fig.update_xaxes(title_text="Time", tickangle=45, nticks=30)
fig.update_layout(autosize=False, width=1100, height=700, legend=dict(title="Lines"), title="All plots")

fig.show()

In [61]:
writer = pd.ExcelWriter(f'frankston-{datetime.now().strftime("%Y_%m_%d-%I_%M_%S_%p")}.xlsx', engine='xlsxwriter')
def write_sheet(data, sheet_presfix = ""):
    for site_name, data in zip(SITE_NAMES, data):
        data["DateTime"] = data["DateTime"].dt.tz_localize(None)
        data.to_excel(writer, sheet_name=f"{sheet_presfix}{site_name}", index=False)
write_sheet(all_merged_data, "Radar-")
rainfall_data["Date/Time"] = rainfall_data["Date/Time"].dt.tz_localize(None)
rainfall_data.to_excel(writer, sheet_name=f"{rain_filename[:31]}", index=False)
writer.close()